# Wrangling and Visualization

In data science, it is often necessary to source data from multiple providers in order to solve a problem.  Each provider may have a different way of expressing data that you might use to merge (dates, names, telephone numbers, etc).

This week's live session will demonstrate these concepts with COVID-19 data from the CDC and Census data from the U.S. Census Bureau.

# COVID Dataset

Load the following dataset from the CDC:

```
COVID_by_State.csv
```

Inspect the data to make sure it looks reasonable

## Scatter Matrix

Select a subset of numerical columns and produce a scatter matrix


## U.S. Plots
2. Plot the time series for the U.S. new cases by date
3. Plot the time series for the U.S. new deaths by date
4. Put both plots on the same graph

## Massachusetts (Breakout)

Repeat the same for the state of Massachusetts

# Census Data

Load the U.S. Census data with population by State:

```
nst-est2019-popchg2010_2019.csv
```

Inspect the data to make sure it looks reasonable

## Cases Per 100,000

1. Compute the total cases per 100,000 person for all 50 states
2. Compute the total deaths per 100,000 person for all 50 states

## Produce Box Plots
1. To show total cases per 100,000 person across all 50 states
2. To show total deaths per 100,000 person across all 50 states

## Scatter Plot
1. Produce a scatter plot of deaths vs cases for all 50 states and place useful Hover tips

## Produce a Paretto (Breakout)
1. Of new cases per 100k of population

In [1]:
import os
import pandas as pd
import numpy as np
import plotly.express as px
import plotly.graph_objects as go

In [2]:
location = '../../data/'
files = os.listdir(location)
files

['CrossStats20150102.txt',
 'multiple_choice.csv',
 'iris_names.txt',
 'iris.csv',
 'nst-est2019-popchg2010-2019.pdf',
 'mount_rainier_daily.csv',
 'COVID_by_State.csv',
 'Candidate Assessment.xlsx',
 'nst-est2019-popchg2010_2019.csv']

In [3]:
from datetime import datetime
dateparse = lambda x: datetime.strptime(x, '%m/%d/%Y')

In [4]:
covid = pd.read_csv(location + 'COVID_by_State.csv',
                   parse_dates=['submission_date'],date_parser=dateparse)

In [5]:
covid.head()

submission_date state  tot_cases  conf_cases  prob_cases  new_case  \
0      2020-12-08    NM     109947         NaN         NaN         0   
1      2021-01-01    FL    1300528         NaN         NaN         0   
2      2020-04-30    IA       7145         NaN         NaN       302   
3      2020-02-26    UT          0         NaN         NaN         0   
4      2020-03-05    GA          2         NaN         NaN        -5   

   pnew_case  tot_death  conf_death  prob_death  new_death  pnew_death  \
0        0.0       1756         NaN         NaN          0         0.0   
1     6063.0      21673         NaN         NaN          0         7.0   
2        0.0        162         NaN         NaN         14         0.0   
3        NaN          0         NaN         NaN          0         NaN   
4        NaN          0         NaN         NaN          0         NaN   

               created_at consent_cases consent_deaths  
0  12/09/2020 02:45:40 PM           NaN      Not agree  
1  01/02/2021 02:50:51 PM     Not agree      Not agree  
2  05/01/2020 09:00:19 PM     Not agree      Not agree  
3  03/26/2020 04:22:39 PM         Agree          Agree  
4  03/26/2020 04:22:39 PM         Agree          Agree

In [6]:
covid.columns

Index(['submission_date', 'state', 'tot_cases', 'conf_cases', 'prob_cases',
       'new_case', 'pnew_case', 'tot_death', 'conf_death', 'prob_death',
       'new_death', 'pnew_death', 'created_at', 'consent_cases',
       'consent_deaths'],
      dtype='object')

# Scatter Matrix

In [7]:
tmp = covid[['tot_cases', 'conf_cases', 'prob_cases',
       'new_case', 'pnew_case', 'tot_death', 'conf_death', 'prob_death',
       'new_death', 'pnew_death']]

In [8]:
fig = px.scatter_matrix(tmp,
                       title='Scatter Matrix')
fig.update_layout(
    dragmode='select',
    width=800,
    height=800,
    hovermode='closest',
)
fig.show()

# New U.S. Cases & Deaths

To plot by date, we need to group by date:

In [27]:
df = covid.groupby('submission_date', as_index=False).sum()
df.head()

submission_date  tot_cases  conf_cases  prob_cases  new_case  pnew_case  \
0      2020-01-22          1         0.0         0.0         1        0.0   
1      2020-01-23          1         0.0         0.0         0        0.0   
2      2020-01-24          2         0.0         0.0         1        0.0   
3      2020-01-25          2         0.0         0.0         0        0.0   
4      2020-01-26          5         0.0         0.0         3        0.0   

   tot_death  conf_death  prob_death  new_death  pnew_death  
0          0         0.0         0.0          0         0.0  
1          0         0.0         0.0          0         0.0  
2          0         0.0         0.0          0         0.0  
3          0         0.0         0.0          0         0.0  
4          0         0.0         0.0          0         0.0

In [26]:
fig = px.line(df, x='submission_date',y='new_case',
             title='Total U.S. COVID Cases<br>2020 to 2021')
fig.show()

### New Deaths

In [28]:
fig = px.line(df, x='submission_date',y='new_death',
             title='Total U.S. COVID Deaths<br>2020 to 2021')
fig.show()

## Both On One Plot

Let's put both case counts and deaths on the same plot:

In [29]:
import plotly.graph_objects as go
from plotly.subplots import make_subplots

fig = make_subplots(specs=[[{"secondary_y": True}]])
fig.add_trace(go.Scatter(x=df['submission_date'], y=df['new_case'],
                    mode='lines',
                    name='Total Cases'),
             secondary_y=False,)

fig.add_trace(go.Scatter(x=df['submission_date'], y=df['new_death'],
                    mode='lines',
                    name='Total Deaths'),
             secondary_y=True)

fig.show()

# Massachusetts

Let's look at the same metrics for the state of Massachusetts.

In [13]:
mass = covid[covid['state'] == 'MA']
mass.head()

submission_date state  tot_cases  conf_cases  prob_cases  new_case  \
75       2020-04-10    MA      20845         NaN         NaN      1904   
115      2020-02-10    MA          1         NaN         NaN         0   
116      2021-01-19    MA     463998    454102.0      9896.0      2567   
151      2020-02-08    MA          1         NaN         NaN         0   
154      2020-04-28    MA      58302     58302.0         0.0      1840   

     pnew_case  tot_death  conf_death  prob_death  new_death  pnew_death  \
75         NaN        599         NaN         NaN         96         NaN   
115        NaN          0         NaN         NaN          0         NaN   
116        0.0      13677     13469.0       208.0         45         0.0   
151        NaN          0         NaN         NaN          0         NaN   
154        0.0       3153      3153.0         0.0        150         0.0   

                 created_at consent_cases consent_deaths  
75   04/09/2020 04:22:39 PM         Agree          Agree  
115  03/26/2020 04:22:39 PM         Agree          Agree  
116  01/20/2021 02:44:03 PM         Agree          Agree  
151  03/26/2020 04:22:39 PM         Agree          Agree  
154  04/29/2020 06:12:08 PM         Agree          Agree

In [14]:
mass.sort_values('submission_date', inplace=True)

<ipython-input-14-877e6218a828>:1: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy



In [31]:
fig = px.line(mass, x='submission_date',y='new_case',
             title='Total Mass. COVID Cases<br>2020 to 2021')
fig.show()

In [32]:
fig = px.line(mass, x='submission_date',y='new_death',
             title='Total U.S. COVID Deaths<br>2020 to 2021')
fig.show()

In [34]:
df = mass
fig = make_subplots(specs=[[{"secondary_y": True}]])
fig.add_trace(go.Scatter(x=df['submission_date'], y=df['new_case'],
                    mode='lines',
                    name='Total Cases'),
             secondary_y=False,)

fig.add_trace(go.Scatter(x=df['submission_date'], y=df['new_death'],
                    mode='lines',
                    name='Total Deaths'),
             secondary_y=True)

fig.show()

# Census Data

## Load & Examine Census Data

Let's start by loading:

In [18]:
census = pd.read_csv(location + 'nst-est2019-popchg2010_2019.csv')

In [19]:
census.head(10)

SUMLEV REGION DIVISION  STATE              NAME  ESTIMATESBASE2010  \
0      10      0        0      0     United States          308758105   
1      20      1        0      0  Northeast Region           55318443   
2      20      2        0      0    Midwest Region           66929725   
3      20      3        0      0      South Region          114563030   
4      20      4        0      0       West Region           71946907   
5      40      3        6      1           Alabama            4780125   
6      40      4        9      2            Alaska             710249   
7      40      4        8      4           Arizona            6392288   
8      40      3        7      5          Arkansas            2916031   
9      40      4        9      6        California           37254519   

   POPESTIMATE2010  POPESTIMATE2011  POPESTIMATE2012  POPESTIMATE2013  ...  \
0        309321666        311556874        313830990        315993715  ...   
1         55380134         55604223         55775216         55901806  ...   
2         66974416         67157800         67336743         67560379  ...   
3        114866680        116006522        117241208        118364400  ...   
4         72100436         72788329         73477823         74167130  ...   
5          4785437          4799069          4815588          4830081  ...   
6           713910           722128           730443           737068  ...   
7          6407172          6472643          6554978          6632764  ...   
8          2921964          2940667          2952164          2959400  ...   
9         37319502         37638369         37948800         38260787  ...   

   NRANK_PPCHG2010  NRANK_PPCHG2011  NRANK_PPCHG2012  NRANK_PPCHG2013  \
0                X                X                X                X   
1                3                3                3                4   
2                4                4                4                3   
3                1                1                1                1   
4                2                2                2                2   
5               37               38               34               33   
6                2                7               11               18   
7               17               10                8                7   
8               22               28               31               38   
9               27               18               20               21   

   NRANK_PPCHG2014  NRANK_PPCHG2015  NRANK_PPCHG2016  NRANK_PPCHG2017  \
0                X                X                X                X   
1                4                4                4                4   
2                3                3                3                3   
3                1                1                1                1   
4                2                2                2                2   
5               35               36               34               33   
6               48               37               22               48   
7                7                9                7                6   
8               31               30               26               24   
9               16               17               20               22   

   NRANK_PPCHG2018  NRANK_PPCHG2019  
0                X                X  
1                4                4  
2                3                3  
3                1                1  
4                2                2  
5               28               26  
6               50               50  
7                4                3  
8               27               27  
9               29               36  

[10 rows x 67 columns]

### Problems

- state==0 is not a state
- sumlev is a filter for aggregation level


In [20]:
census.columns

Index(['SUMLEV', 'REGION', 'DIVISION', 'STATE', 'NAME', 'ESTIMATESBASE2010',
       'POPESTIMATE2010', 'POPESTIMATE2011', 'POPESTIMATE2012',
       'POPESTIMATE2013', 'POPESTIMATE2014', 'POPESTIMATE2015',
       'POPESTIMATE2016', 'POPESTIMATE2017', 'POPESTIMATE2018',
       'POPESTIMATE2019', 'NPOPCHG_2010', 'NPOPCHG_2011', 'NPOPCHG_2012',
       'NPOPCHG_2013', 'NPOPCHG_2014', 'NPOPCHG_2015', 'NPOPCHG_2016',
       'NPOPCHG_2017', 'NPOPCHG_2018', 'NPOPCHG_2019', 'PPOPCHG_2010',
       'PPOPCHG_2011', 'PPOPCHG_2012', 'PPOPCHG_2013', 'PPOPCHG_2014',
       'PPOPCHG_2015', 'PPOPCHG_2016', 'PPOPCHG_2017', 'PPOPCHG_2018',
       'PPOPCHG_2019', 'NRANK_ESTBASE2010', 'NRANK_POPEST2010',
       'NRANK_POPEST2011', 'NRANK_POPEST2012', 'NRANK_POPEST2013',
       'NRANK_POPEST2014', 'NRANK_POPEST2015', 'NRANK_POPEST2016',
       'NRANK_POPEST2017', 'NRANK_POPEST2018', 'NRANK_POPEST2019',
       'NRANK_NPCHG2010', 'NRANK_NPCHG2011', 'NRANK_NPCHG2012',
       'NRANK_NPCHG2013', 'NRANK_NPCHG2014',

In [21]:
census.iloc[0]

SUMLEV                        10
REGION                         0
DIVISION                       0
STATE                          0
NAME               United States
                       ...      
NRANK_PPCHG2015                X
NRANK_PPCHG2016                X
NRANK_PPCHG2017                X
NRANK_PPCHG2018                X
NRANK_PPCHG2019                X
Name: 0, Length: 67, dtype: object

In [22]:
sub = census[census['SUMLEV'] == 40]

In [23]:
sub = sub[['NAME','POPESTIMATE2019']]
sub.head()

NAME  POPESTIMATE2019
5     Alabama          4903185
6      Alaska           731545
7     Arizona          7278717
8    Arkansas          3017804
9  California         39512223

# Merge

OOPS, the Census dataset shows states fully spelled out but the COVID dataset shows states as a two letter acronym

In [24]:
covid.head()

submission_date state  tot_cases  conf_cases  prob_cases  new_case  \
0      2020-12-08    NM     109947         NaN         NaN         0   
1      2021-01-01    FL    1300528         NaN         NaN         0   
2      2020-04-30    IA       7145         NaN         NaN       302   
3      2020-02-26    UT          0         NaN         NaN         0   
4      2020-03-05    GA          2         NaN         NaN        -5   

   pnew_case  tot_death  conf_death  prob_death  new_death  pnew_death  \
0        0.0       1756         NaN         NaN          0         0.0   
1     6063.0      21673         NaN         NaN          0         7.0   
2        0.0        162         NaN         NaN         14         0.0   
3        NaN          0         NaN         NaN          0         NaN   
4        NaN          0         NaN         NaN          0         NaN   

               created_at consent_cases consent_deaths  
0  12/09/2020 02:45:40 PM           NaN      Not agree  
1  01/02/2021 02:50:51 PM     Not agree      Not agree  
2  05/01/2020 09:00:19 PM     Not agree      Not agree  
3  03/26/2020 04:22:39 PM         Agree          Agree  
4  03/26/2020 04:22:39 PM         Agree          Agree

# Load 3rd Dataset

This third dataset contains state codes

In [36]:
states = pd.read_csv(location + 'state_codes.csv')
states.head()

State  Abbrev Code
0     Alabama    Ala.   AL
1      Alaska  Alaska   AK
2     Arizona   Ariz.   AZ
3    Arkansas    Ark.   AR
4  California  Calif.   CA

# Add State Code to Census

In [37]:
full_states = pd.merge(sub, states, left_on='NAME', right_on='State')
full_states.head()

NAME  POPESTIMATE2019       State  Abbrev Code
0     Alabama          4903185     Alabama    Ala.   AL
1      Alaska           731545      Alaska  Alaska   AK
2     Arizona          7278717     Arizona   Ariz.   AZ
3    Arkansas          3017804    Arkansas    Ark.   AR
4  California         39512223  California  Calif.   CA

In [38]:
sub = full_states[['NAME','POPESTIMATE2019','Code']]
sub.head()

NAME  POPESTIMATE2019 Code
0     Alabama          4903185   AL
1      Alaska           731545   AK
2     Arizona          7278717   AZ
3    Arkansas          3017804   AR
4  California         39512223   CA

In [39]:
cov = pd.merge(covid, sub, left_on='state', right_on='Code',)
cov.head()

submission_date state  tot_cases  conf_cases  prob_cases  new_case  \
0      2020-12-08    NM     109947         NaN         NaN         0   
1      2020-03-17    NM         23         NaN         NaN         2   
2      2020-11-06    NM      52394         NaN         NaN      1284   
3      2020-04-27    NM       2823         NaN         NaN        97   
4      2020-12-10    NM     114731         NaN         NaN      1781   

   pnew_case  tot_death  conf_death  prob_death  new_death  pnew_death  \
0        0.0       1756         NaN         NaN          0         0.0   
1        NaN          0         NaN         NaN          0         NaN   
2        0.0       1088         NaN         NaN          6         0.0   
3        0.0        104         NaN         NaN          5         0.0   
4        0.0       1846         NaN         NaN         23         0.0   

               created_at consent_cases consent_deaths        NAME  \
0  12/09/2020 02:45:40 PM           NaN      Not agree  New Mexico   
1  03/26/2020 04:22:39 PM           NaN      Not agree  New Mexico   
2  11/07/2020 02:45:17 PM           NaN      Not agree  New Mexico   
3  05/25/2020 03:38:40 PM           NaN      Not agree  New Mexico   
4  12/11/2020 03:06:51 PM           NaN      Not agree  New Mexico   

   POPESTIMATE2019 Code  
0          2096829   NM  
1          2096829   NM  
2          2096829   NM  
3          2096829   NM  
4          2096829   NM

In [40]:
cov['tot_cases_per_100k'] = cov['tot_cases'] / cov['POPESTIMATE2019'] * 100000
cov['tot_death_per_100k'] = cov['tot_death'] / cov['POPESTIMATE2019'] * 100000

In [41]:
max(cov['submission_date'])

Timestamp('2021-03-13 00:00:00')

In [42]:
last = cov[cov['submission_date'] == '2021-03-13']
len(last)

51

In [43]:
last

submission_date state  tot_cases  conf_cases  prob_cases  new_case  \
336        2021-03-13    NM     188167         NaN         NaN       183   
774        2021-03-13    FL    1936788         NaN         NaN      5175   
936        2021-03-13    IA     342495         NaN         NaN       425   
1616       2021-03-13    UT     377983    377983.0         0.0       491   
1738       2021-03-13    GA    1032967    834696.0    198271.0      1254   
2397       2021-03-13    WV     135149    107786.0     27363.0       307   
2816       2021-03-13    TN     791282    659645.0    131637.0      1630   
3180       2021-03-13    NY     961370         NaN         NaN      3147   
3603       2021-03-13    AR     326813         NaN         NaN       314   
3876       2021-03-13    OK     432340    342483.0     89857.0       349   
4230       2021-03-13    HI      27334         NaN         NaN        62   
4693       2021-03-13    CO     442753    416890.0     25863.0      1242   
5347       2021-03-13    SD     114493         NaN         NaN       146   
5616       2021-03-13    KS     297748    241369.0     56379.0         0   
6050       2021-03-13    OH     988298    842626.0    145672.0      1558   
6257       2021-03-13    PA     964296    826084.0    138212.0      2840   
6733       2021-03-13    TX    2715755         NaN         NaN      4906   
7186       2021-03-13    MA     577004    567108.0      9896.0      1548   
7801       2021-03-13    AK      57784         NaN         NaN         0   
7944       2021-03-13    KY     415770    317805.0     97965.0       679   
8715       2021-03-13    NH      78319         NaN         NaN       245   
9146       2021-03-13    SC     530736    453283.0     77453.0       812   
9258       2021-03-13    NJ     834715    739249.0     95466.0      4034   
9864       2021-03-13    DC      42432         NaN         NaN       150   
10187      2021-03-13    NE     204464         NaN         NaN       302   
10529      2021-03-13    CA    3523563         NaN         NaN      3230   
10969      2021-03-13    MT     101726     95286.0      6440.0       170   
11287      2021-03-13    NC     882715    766961.0    115754.0       892   
11776      2021-03-13    IL    1207847   1207847.0         0.0      1675   
12265      2021-03-13    MI     670088    607437.0     62651.0      2003   
12841      2021-03-13    WA     349425         NaN         NaN       909   
13269      2021-03-13    AL     503305    394421.0    108884.0       594   
13647      2021-03-13    OR     159392    159392.0         0.0       355   
14069      2021-03-13    DE      90156     85284.0      4872.0       245   
14505      2021-03-13    MS     300780    185617.0    115163.0       203   
14728      2021-03-13    WY      55163     46714.0      8449.0         0   
15161      2021-03-13    ME      47025     36546.0     10479.0       169   
15718      2021-03-13    VA     594735    467995.0    126740.0      1173   
15859      2021-03-13    ID     175236    141312.0     33924.0       293   
16624      2021-03-13    AZ     832094    774490.0     57604.0       262   
17084      2021-03-13    IN     671859         NaN         NaN       836   
17180      2021-03-13    MO     566386         NaN         NaN       518   
17624      2021-03-13    ND     100976     95303.0      5673.0        34   
18197      2021-03-13    LA     436482         NaN         NaN         0   
18358      2021-03-13    WI     625045    569364.0     55681.0       537   
19099      2021-03-13    MN     496395         NaN         NaN      1187   
19200      2021-03-13    CT     290577    270354.0     20223.0         0   
19836      2021-03-13    MD     393441         NaN         NaN       860   
20203      2021-03-13    VT      16698         NaN         NaN        75   
20508      2021-03-13    RI     130502         NaN         NaN         0   
20911      2021-03-13    NV     299065         NaN         NaN       442   

       pnew_case  tot_death  conf_death  prob_death  

In [44]:
ss = last[['NAME','Code','POPESTIMATE2019','tot_cases_per_100k','tot_death_per_100k']]
ss.columns = ['name','code','population','tot_cases_per_100k','tot_death_per_100k']
ss

name code  population  tot_cases_per_100k  \
336              New Mexico   NM     2096829         8973.883898   
774                 Florida   FL    21477737         9017.653955   
936                    Iowa   IA     3155070        10855.385142   
1616                   Utah   UT     3205958        11790.017212   
1738                Georgia   GA    10617423         9728.980375   
2397          West Virginia   WV     1792147         7541.178263   
2816              Tennessee   TN     6829174        11586.789266   
3180               New York   NY    19453561         4941.871568   
3603               Arkansas   AR     3017804        10829.497211   
3876               Oklahoma   OK     3956971        10926.034080   
4230                 Hawaii   HI     1415872         1930.541744   
4693               Colorado   CO     5758736         7688.371198   
5347           South Dakota   SD      884659        12942.048857   
5616                 Kansas   KS     2913314        10220.250890   
6050                   Ohio   OH    11689100         8454.868211   
6257           Pennsylvania   PA    12801989         7532.392037   
6733                  Texas   TX    28995881         9366.002709   
7186          Massachusetts   MA     6892503         8371.472599   
7801                 Alaska   AK      731545         7898.898906   
7944               Kentucky   KY     4467673         9306.186912   
8715          New Hampshire   NH     1359711         5759.973994   
9146         South Carolina   SC     5148714        10308.127428   
9258             New Jersey   NJ     8882190         9397.626036   
9864   District of Columbia   DC      705749         6012.335830   
10187              Nebraska   NE     1934408        10569.848760   
10529            California   CA    39512223         8917.653153   
10969               Montana   MT     1068778         9517.972862   
11287        North Carolina   NC    10488084         8416.360891   
11776              Illinois   IL    12671821         9531.755539   
12265              Michigan   MI     9986857         6709.698557   
12841            Washington   WA     7614893         4588.705317   
13269               Alabama   AL     4903185        10264.858454   
13647                Oregon   OR     4217737         3779.088170   
14069              Delaware   DE      973764         9258.506168   
14505           Mississippi   MS     2976149        10106.348842   
14728               Wyoming   WY      578759         9531.255669   
15161                 Maine   ME     1344212         3498.332108   
15718              Virginia   VA     8535519         6967.766108   
15859                 Idaho   ID     1787065         9805.798894   
16624               Arizona   AZ     7278717        11431.877349   
17084               Indiana   IN     6732219         9979.755561   
17180              Missouri   MO     6137428         9228.393392   
17624          North Dakota   ND      762062        13250.365456   
18197             Louisiana   LA     4648794         9389.144798   
18358             Wisconsin   WI     5822434        10735.115246   
19099             Minnesota   MN     5639632         8801.904096   
19200           Connecticut   CT     3565287         8150.171361   
19836              Maryland   MD     6045680         6507.803919   
20203               Vermont   VT      623989         2676.008712   
20508          Rhode Island   RI     1059361        12318.935660   
20911                Nevada   NV     3080156         9709.410822   

       tot_death_per_100k  
336            183.610585  
774            150.039085  
936            178.538036  
1616            63.038879  
1738           171.567055  
2397           140.557666  
2816           170.254851  
3180            94.543102  
3603           180.760580  
3876           120.824742  
4230            31.570650  
4693           104.814668  
5347           215.789361  
5616           165.584623  
6050           154.297593  
6257           191.946736  
6733      

# Scatter Plot

In [47]:
fig = px.scatter(ss, x='tot_cases_per_100k',y='tot_death_per_100k',
                 hover_name="name", hover_data=["population", "tot_cases_per_100k","tot_death_per_100k"],
                 title="U.S. COVID 19 Deaths vs Cases<br>Normalized By State"
                )

fig.show()

In [48]:
ss.sort_values('tot_cases_per_100k', inplace=True, ascending=False)

<ipython-input-48-a1d9e7977ecf>:1: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy



In [49]:
fig = px.bar(ss, x='name', y='tot_cases_per_100k',
            title='Pareto of Cases By 100k')
fig.show()

In [52]:
ss.sort_values('tot_death_per_100k', inplace=True, ascending=False)

<ipython-input-52-3bc45dc69041>:1: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy



In [53]:
fig = px.bar(ss, x='name', y='tot_death_per_100k',
            title='Pareto of Cases By 100k')
fig.show()